In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [ ]:
df = pd.read_csv('../duplicated_new.csv')

In [ ]:
df = df[df['genres'] != '[]']
genre_dict = {}
artist_dict = {}
for index, row in df.iterrows():
    artist = row['artists']
    genres_str = row['genres'][1:-1]
    genres = genres_str.split("', '")
    for i in range(len(genres)):
        genres[i] = genres[i].strip(" ''")
    for g in genres:
        if g not in genre_dict:
            genre_dict[g] = [artist]
        else:
            genre_dict[g].append(artist)
    artist_dict[artist] = genres

In [ ]:
genre_dict_counts = {}
for k in genre_dict:
    genre_dict_counts[k] = len(genre_dict[k])
sorted_counts = sorted(genre_dict_counts.items(), key=lambda item: item[1])
top_counts = dict(sorted_counts[-30:])
print(len(genre_dict_counts.keys()))

In [ ]:
plt.bar(top_counts.keys(), top_counts.values())
plt.xticks(rotation=90)
plt.xlabel('genres') 
plt.ylabel('artist counts') 
plt.title("30 top genres on spotify")

In [42]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
from spotipy.oauth2 import SpotifyOAuth
import pandas as pd

In [43]:
CLIENT_ID = '19cf2d65b83d438e98e9e10b8c809962'
CLIENT_SECRET = '809228d3677a4f32aefb22879f580f15'

client_credentials_manager = SpotifyClientCredentials(client_id=CLIENT_ID,
                                                      client_secret=CLIENT_SECRET)
sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager)

In [ ]:
data_dict_compiled = df.to_dict()
data_dict_compiled.keys()

In [ ]:
data_dict_compiled['songs'] = []
data_dict_compiled['followers'] = []
data_dict_compiled['Popularity Score'] = []
data_dict_compiled['Artist ID'] = []
data_dict_compiled['Image URL'] = []
for index, row in df.iterrows():
    artist = row['artists']
    genres = row['genres']
    results = sp.search(q='artist:' + artist, type='artist')
    items = results['artists']['items']
    song_list = []
    artist_url = []
    popularity = -1
    followers = -1
    image_url = ''
    artist_uri = ''
    if items != []:
        artist_uri = items[0]['id']
        popularity = items[0]['popularity']
        followers = items[0]['followers']['total']
        images = items[0]['images']
        if images != []:
            image_url = images[0]['url']
        tracks = sp.artist_top_tracks(artist_uri,country='US')['tracks']
        for t in range(0,len(tracks)):
            song_list.append(tracks[t]['name'])
    print(index)
    data_dict_compiled['songs'].append((song_list))
    data_dict_compiled['followers'].append(followers)
    data_dict_compiled['Popularity Score'].append(popularity)
    data_dict_compiled['Artist ID'].append(artist_uri)
    data_dict_compiled['Image URL'].append(image_url)

In [ ]:
data_dict_compiled['artists'] = data_dict_compiled['artists'].values()

In [ ]:
data_dict_compiled['acousticness'] = data_dict_compiled['acousticness'].values()

In [ ]:
data_dict_compiled['danceability'] = data_dict_compiled['danceability'].values()
data_dict_compiled['duration_ms'] = data_dict_compiled['duration_ms'].values()
data_dict_compiled['energy'] = data_dict_compiled['energy'].values()
data_dict_compiled['instrumentalness'] = data_dict_compiled['instrumentalness'].values()
data_dict_compiled['liveness'] = data_dict_compiled['liveness'].values()
data_dict_compiled['loudness'] = data_dict_compiled['loudness'].values()
data_dict_compiled['speechiness'] = data_dict_compiled['speechiness'].values()
data_dict_compiled['tempo'] = data_dict_compiled['tempo'].values()
data_dict_compiled['valence'] = data_dict_compiled['valence'].values()
data_dict_compiled['popularity'] = data_dict_compiled['popularity'].values()
data_dict_compiled['key'] = data_dict_compiled['key'].values()
data_dict_compiled['mode'] = data_dict_compiled['mode'].values()
data_dict_compiled['count'] = data_dict_compiled['count'].values()
data_dict_compiled['genres'] = data_dict_compiled['genres'].values()

In [ ]:
df_data_dict_compiled = pd.DataFrame.from_dict(data_dict_compiled)

In [ ]:
df_data_dict_compiled.to_csv('cs4300sp2021-ag2496-cc972-mb2359-jjz67-jxl8/data/processed/compiled-w-songs_new.csv')

In [ ]:
df_check = pd.read_csv('../data/processed/compiled-w-songs_new.csv')

In [ ]:
duplicates_new = df_check[df_check.duplicated('songs')]
duplicates_new = duplicates_new[['artists','songs']]
duplicates_new = duplicates_new.sort_values(by=['songs'])

In [ ]:
duplicates_new.to_csv('../duplicated_new.csv')

In [ ]:
removed_dups = df_check.drop_duplicates(subset =['songs'], keep = 'last')

In [ ]:
removed_dups = removed_dups[removed_dups['Popularity Score'] >= 60]
length_lst = []
for index, row in removed_dups.iterrows():
    songs_str = row['songs']
    songs = songs_str.replace('"', "'").strip("'[]").split("', '")
    length_lst.append(len(songs))
removed_dups['Length'] = length_lst
removed_dups = removed_dups[removed_dups['Length'] == 10]
removed_dups = removed_dups.iloc[:4013]
removed_dups['artists'] = removed_dups['artists'].replace(['We'],['The Weeknd'])

In [ ]:
removed_dups.to_csv('../removed_dups_new.csv')

In [44]:
removed_dups = pd.read_csv('../removed_dups_new_extra.csv')

In [37]:
removed_dups = removed_dups[['artists','genres','followers','Artist ID','Popularity Score','Image URL']]

In [38]:
removed_dups.head()

artists                                             genres  \
0  "Weird Al" Yankovic                 ['comedy rock', 'comic', 'parody']   
1          $atori Zoom                          ['dark trap', 'meme rap']   
2          $uicideBoy$  ['dark trap', 'new orleans rap', 'underground ...   
3             (G)I-DLE                      ['k-pop', 'k-pop girl group']   
4               *NSYNC        ['boy band', 'dance pop', 'europop', 'pop']   

   followers               Artist ID  Popularity Score  \
0     552324  1bDWGdIC2hardyt55nlQgG                60   
1      27590  75RLThQWzIgIM7Jtp6KZic                62   
2    3138167  1VPmR4DJC1PlOtd0IADAO0                85   
3    2456936  2AfmfGFbe0A0WsTYm0SDTx                76   
4    1480467  6Ff53KvcvAj5U7Z1vojB5o                71   

                                           Image URL  
0  https://i.scdn.co/image/b0813085ef7141d31b4744...  
1  https://i.scdn.co/image/ab6761610000e5eb5c2a22...  
2  https://i.scdn.co/image/2d1e0c2edbb23b01d494b2...  
3  https://i.scdn.co/image/6744b6a37d1c29cb5fc626...  
4  https://i.scdn.co/image/c56cf0cc89c8ecfec7145c...

In [39]:
removed_dups.to_csv('../removed_dups_new.csv')

In [49]:
birdy_uri = 'spotify:artist:2WX2uTcsvV5OnS0inACecP'
results = sp.artist_albums(birdy_uri, album_type='album')
albums = results['items']
while results['next']:
    results = spotify.next(results)
    albums.extend(results['items'])

for album in albums:
    print(album['name'])

Young Heart
Beautiful Lies
Beautiful Lies
Beautiful Lies (Deluxe)
Beautiful Lies (Deluxe)
Fire Within
Fire Within
Fire Within (Deluxe)
Fire Within (Deluxe)
Fire Within (Deluxe)
Live in London
Birdy
Birdy
Birdy
Birdy
Birdy (Deluxe Version)


In [51]:
album_list = []
for index, row in removed_dups.iterrows():
    artistid = row['Artist ID']
    results = sp.artist_albums(artistid, album_type='album')
    albums = results['items']
    albumlst = []
    while results['next']:
        results = sp.next(results)
        albums.extend(results['items'])
    for a in albums:
        albumlst.append(a['name'])
    print(albumlst)
    album_list.append(albumlst)
removed_dups['Albums'] = album_list

['The Idiots Are Winning (Live 1984)', 'Mandatory Fun', 'Alpocalypse', 'Straight Outta Lynwood', 'Poodle Hat', 'Running With Scissors', 'Bad Hair Day', 'Alapalooza', 'Off The Deep End', 'UHF: "Weird Al" Yankovic', 'Even Worse', 'Polka Party', 'Dare To Be Stupid', 'In 3-D', '"Weird Al" Yankovic']
['SADIE AND ALL HER FRIENDS', 'Phase 4: The Final Chapter', 'Phase 3: Psychosis', 'Phase 2: Disillusion', 'Phase 1: Self Destructive']
['Stop Staring at the Shadows', 'I Want to Die In New Orleans', 'Eternal Grey', 'Grey Sheep II', 'Dark Side of the Clouds', "Now the Moon's Rising", "My Liver Will Handle What My Heart Can't", 'Grey Sheep', "High Tide in the Snake's Nest", 'YUNGDEATHLILLIFE', '7th or St. Tammany', 'Black $uicide Side B: $uicide Hustle', 'Gray/Grey', 'KILL YOURSELF Part X: The Resurrection Saga', 'KILL YOURSELF Part VII: The Fuck God Saga']
[]
['The Meaning Of Christmas', 'Celebrity', 'Celebrity', 'Celebrity', 'No Strings Attached', 'No Strings Attached', 'No Strings Attached', '

In [31]:
removed_dups['Album'] = album_list

In [89]:
len(album_list[3346])

62

In [95]:
new_a_list = []
for a in range(len(album_list)):
    alb = list(set(album_list[a]))
    if len(alb) > 50:
        new_a_list.append([])
    else:
        for album in range(len(alb)):
            name = alb[album]
            if ' (' in name:
                index = name.index(' (')
                alb[album] = name[:index]
        new_a_list.append(list(set(alb)))

In [104]:
print(new_a_list[15])

['To Anyone', '2NE1 1st LIVE CONCERT [NOLZA!]', 'COLLECTION', '2NE1 1st Japan Tour "NOLZA in Japan"', '2014 2NE1 WORLD TOUR 〜ALL OR NOTHING〜 in JAPAN', '2NE1', '2NE1 1st Mini Album', '2014 2NE1 World Tour Live - All Or Nothing In Seoul', '2012 2NE1 Global Tour Live New Evolution in Seoul', '2NE1 BEST COLLECTION', '2NE1 1ST LIVE CONCERT [ NOLZA! ]', '2NE1 2012 1st Global Tour - NEW EVOLUTION in Japan', '2014 2NE1 WORLD TOUR ~ALL OR NOTHING~ in JAPAN', 'CRUSH']


In [106]:
print(set(album_list[15]))

{'To Anyone', '2NE1 1st LIVE CONCERT [NOLZA!]', 'COLLECTION', '2NE1 1st Japan Tour "NOLZA in Japan"', '2014 2NE1 WORLD TOUR 〜ALL OR NOTHING〜 in JAPAN', '2NE1', '2NE1 1st Mini Album', '2014 2NE1 World Tour Live - All Or Nothing In Seoul', '2012 2NE1 Global Tour Live New Evolution in Seoul', '2NE1 BEST COLLECTION', '2NE1 1ST LIVE CONCERT [ NOLZA! ]', '2NE1 2012 1st Global Tour - NEW EVOLUTION in Japan', '2014 2NE1 WORLD TOUR ~ALL OR NOTHING~ in JAPAN', 'CRUSH'}


In [76]:
import pitchfork

In [80]:
print(len(removed_dups['artists']))

4013


In [102]:
descriptors = {}
ratings = {}
albums_dict = {}

In [116]:
for i in range(3470,4013):
    artist = removed_dups['artists'][i]
    albums = new_a_list[i][:2]
    print(i, artist)
    print(albums)
    for album in albums:
        try:
            a = album[:3]
            p = pitchfork.search(artist,a)
            abstract = p.abstract()
            rating = p.score()
            descriptors[artist] = abstract
            ratings[artist] = rating
            albums_dict[artist] = p.album()
            break
        except IndexError:
            continue

3470 The Mountain Goats
['All Eternals Deck', 'We Shall All Be Healed']
3471 The Mowgli's
['Waiting For The Dawn', "Where'd Your Weekend Go?"]
3472 The Naked And Famous
['Passive Me, Aggressive You', 'Recover']
3473 The National
['Sad Songs for Dirty Lovers', 'I Am Easy to Find']
3474 The Neighbourhood
['I Love You.', 'Chip Chrome & The Mono-Tones']
3475 The Noise Project
['Perfect Noises Of Waves And Water For Delicious Deep Relaxation', 'Beautiful White Noise Of Nature And Animals For Instant Deep Sleep']
3476 The Notorious B.I.G.
['Ready to Die', 'Duets: The Final Chapter']
3477 The O'Jays
["Christmas With The O'Jays", 'Message In The Music']
3478 The O'Neill Brothers Group
[]
3479 The Offspring
['Conspiracy Of One', 'Ixnay On The Hombre']
3480 The Oh Hellos
['Through the Deep, Dark Valley', 'Boreas']
3481 The Orion Experience
['Cosmicandy', 'Children of the Stars']
3482 The Outfield
["Live in Brazil '01", "It Ain't Over"]
3483 The Paper Kites
['twelvefour', 'On the Train Ride Home'

In [117]:
print(len(albums_dict))

914


In [132]:
df = removed_dups.iloc[1646:]

In [133]:
df.head()

Unnamed: 0  Unnamed: 0.1           artists  acousticness  danceability  \
1646        8192          8192  Johannes Bornlöf      0.978857      0.303000   
1647        8193          8193   Johannes Brahms      0.937321      0.287496   
1648        8205          8205        John Barry      0.751538      0.175152   
1649        8216          8216     John Coltrane      0.687756      0.461802   
1650        8226          8226       John Denver      0.729214      0.447145   

        duration_ms    energy  instrumentalness  liveness   loudness  ...  \
1646  358997.571429  0.071614          0.889143  0.104214 -26.142143  ...   
1647  420610.957792  0.167382          0.691404  0.164618 -18.552938  ...   
1648  187220.490385  0.153106          0.823092  0.136413 -19.777952  ...   
1649  432675.035573  0.353689          0.149628  0.176713 -13.159984  ...   
1650  197334.189516  0.281738          0.008964  0.193592 -13.604214  ...   

      count                                             genres  \
1646     14  ['background music', 'calming instrumental', '...   
1647    308  ['classical', 'german romanticism', 'late roma...   
1648    104  ['adult standards', 'british soundtrack', 'cla...   
1649    506  ['bebop', 'contemporary post-bop', 'cool jazz'...   
1650    248  ['adult standards', 'classic country pop', 'fo...   

                                                  songs  followers  \
1646  ['Reminiscence', 'Streams', 'Immersed', "Let's...      36741   
1647  ['Sechs Klavierstücke, Op. 118: II. Intermezzo...     690326   
1648  ['The John Dunbar Theme (film version)', 'Some...      72514   
1649  ['In A Sentimental Mood', 'My Little Brown Boo...    1274792   
1650  ['Take Me Home, Country Roads', "Annie's Song"...    1246746   

      Popularity Score               Artist ID  \
1646                64  1yLIaxyVkZnLMXhfRSYEjV   
1647                66  5wTAi7QkpP6kp8a54lmTOq   
1648                61  7ctAOUlIAs7yuMODWE2Fyz   
1649                69  2hGh5VOeeqimQFxqXvfCUf   
1650                73  7EK1bQADBoqbYXnT4Cqv9w   

                                              Image URL Length  \
1646  https://i.scdn.co/image/bfc064cf92ff7930b0fbf1...     10   
1647  https://i.scdn.co/image/d5c6af18beb1411ab49c29...     10   
1648  https://i.scdn.co/image/b708e6e1afb8fc2b82c887...     10   
1649  https://i.scdn.co/image/b5958fbd911c9ada338a50...     10   
1650  https://i.scdn.co/image/2e3013f80d3e7386063d4c...     10   

                                                 Albums  \
1646  [TV Soundtracks, TV Soundtracks, TV Soundtrack...   
1647  [Simply Brahms, Storia della musica classica -...   
1648  [Oldies Selection: Last Collection 2019 (Remas...   
1649  [On Impulse: John Coltrane, Giant Steps (60th ...   
1650  [Shelter From The Storm (Live 1982), Colorado ...   

                                                  Album  
1646  [The 50 Greatest Epic Piano Pieces, TV Soundtr...  
1647                                                 []  
1648                                                 []  
1649                                                 []  
1650                                                 []  

[5 rows x 26 columns]

In [134]:
df = removed_dups.loc[removed_dups['Popularity Score'] > 79]

In [125]:
new_a2_list = []
for a in range(len(album_list)):
    alb = list(set(album_list[a]))
    for album in range(len(alb)):
        name = alb[album]
        if ' (' in name:
            index = name.index(' (')
            alb[album] = name[:index]
    new_a2_list.append(list(set(alb)))

In [136]:
for index,row in df.iterrows():
    artist = row['artists']
    if index >= 1646:
        if artist not in albums_dict:
            albums = new_a2_list[index]
            print(index, artist)
            print(albums)
            for album in albums:
                try:
                    a = album[:3]
                    p = pitchfork.search(artist,a)
                    abstract = p.abstract()
                    rating = p.score()
                    descriptors[artist] = abstract
                    ratings[artist] = rating
                    albums_dict[artist] = p.album()
                    break
                except IndexError:
                    continue

1655 John Legend
['Wake Up!', "Live at SOB's", 'Evolver', 'Bigger Love', 'A Legendary Christmas', 'Get Lifted', 'DARKNESS AND LIGHT', 'Once Again', 'Love In The Future', 'Spotify Sessions']
1658 John Mayer
['Born and Raised', 'Inside Wants Out', 'As/Is: Live In Mountain View, CA - 7/16/04', 'As/Is: Live In Cleveland/Cincinnati, OH - 8/03-8/04/04', 'Any Given Thursday', 'As/Is: Live In Houston, TX - 7/24/04', 'Continuum', 'Room For Squares', 'As/Is - Live', 'Battle Studies', 'The Search for Everything', 'Where the Light Is: John Mayer Live In Los Angeles', 'Paradise Valley', 'Heavier Things', 'As/Is: Houston, TX - 7/24/04', 'As/Is: Live In Philadelphia, PA/Hartford, CT - 8/14-8/15/04']
1681 Jonas Blue
['EST. 1989', 'Blue']
1723 Juhn
[]
1742 Justin Bieber
['My Worlds', 'Under The Mistletoe', 'My World 2.0', 'My Worlds Acoustic', 'Changes', 'My World', 'Journals', 'Purpose', 'Never Say Never - The Remixes', 'Believe', 'Justice', 'Believe Acoustic']
1745 Justin Quiles
['Realidad', 'Imperio

In [167]:
descriptors['Kanye West']

"The producer-rapper follows his Pazz and Jop-winning debut The College Dropout with a collaboration with Jon Brion; together they transform West's chattering, seemingly unrealistic ideas into an expansive, imperfect masterpiece.\n"

In [169]:
import json

In [170]:
with open('descriptors_final.json', 'w') as outfile: # plug in numbers
    json.dump(descriptors, outfile)
with open('ratings_final.json', 'w') as outfile: # plug in numbers
    json.dump(ratings, outfile)
with open('albums_final.json', 'w') as outfile: # plug in numbers
    json.dump(albums_dict, outfile)